In [1]:
!pip install english-words

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.2/8.2 MB 52.3 MB/s eta 0:00:00
  Installing build dependencies ... - \ | / - done
  Getting requirements to build wheel ... - done
  Preparing metadata (pyproject.toml) ... - done
  Created wheel for english-words: filename=english_words-2.0.1-py3-none-any.whl size=8196238 sha256=6ec9cf6aa04ad6a565ea2827d33ae23221982c7a2e9e640ddeef8cc405f16c66
  Stored in directory: /root/.cache/pip/wheels/f0/e6/d9/16a123647999fe535f03a36e7af23eef203736d84c7ca25b0b
Successfully built english-words


In [2]:
import pandas as pd
df = pd.read_csv(filepath_or_buffer='/kaggle/input/hate-speech-and-offensive-language-detection/train.csv',
                usecols=['tweet'])
df.head()

tweet
0  !!! RT @mayasolovely: As a woman you shouldn't...
1  !!!!! RT @mleew17: boy dats cold...tyga dwn ba...
2  !!!!!!! RT @UrKindOfBrand Dawg!!!! RT @80sbaby...
3  !!!!!!!!! RT @C_G_Anderson: @viva_based she lo...
4  !!!!!!!!!!!!! RT @ShenikaRoberts: The shit you...

In [3]:
stopwords_df = pd.read_csv(filepath_or_buffer='/kaggle/input/nltk-english-stopwords/nltk_eng_stopwords.csv')
stopwords = stopwords_df['list_of_stopwords'].values.tolist() 

In [4]:
from english_words import get_english_words_set
web2lowerset = get_english_words_set(['web2'], lower=True)
len(web2lowerset)

234450

In [5]:
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer

WIDTH = 60
def make(input_df: pd.DataFrame, column: str, stopwords: set, vocabulary: set, width: int):
    model_ = CountVectorizer(stop_words=stopwords, vocabulary=vocabulary)
    count_ = model_.fit_transform(raw_documents=input_df[column])
    result_df = pd.DataFrame(data={'word' : model_.get_feature_names_out(), 
                                   'count' : count_.toarray().sum(axis=0)})
    result_df = result_df.sort_values(ascending=False, by='count').reset_index(drop=True)
    result_df['x'] = [index % width for index in result_df.index.tolist()]
    result_df['log count'] = result_df['count'].apply(np.log)
    return result_df

stopword_df = make(input_df=df, column='tweet', stopwords=None, vocabulary=stopwords, width=WIDTH)
print('counted stopwords.')
web2_df = make(input_df=df, column='tweet', stopwords=stopwords, vocabulary=web2lowerset, width=WIDTH)
print('counted dictionary words.')
residue_df = make(input_df=df, column='tweet', stopwords=stopwords + list(web2lowerset), vocabulary=None, width=WIDTH)
print('counted residue.')

counted stopwords.
counted dictionary words.
counted residue.


In [6]:
from plotly.express import histogram
histogram(data_frame=stopword_df, x='count', log_y=True)

In [7]:
from plotly.express import scatter
scatter(data_frame=stopword_df, x='x', y='count', text='word', log_y=True).update_traces(marker={'size': 1})

In [8]:
from plotly.express import scatter
for input_df in [stopword_df, web2_df, residue_df]:
    scatter(data_frame=input_df, x='x', y='count', hover_name='word', color='log count', log_y=True).show()

In [9]:
numeric_df = residue_df[residue_df['word'].str.isnumeric()]
numeric_df.head(n=10)

word  count   x  log count
1   128514   3241   1   8.083637
6     8220   1726   6   7.453562
7     8221   1682   7   7.427739
10    8230   1265  10   7.142827
15  128557    616  15   6.423247
19  128553    368  19   5.908083
23  128175    311  23   5.739793
27    8217    283  27   5.645447
31   65039    273  31   5.609472
32  128530    264  32   5.575949